---

# S04E02 : Context managers - The *contextlib* module

Cyril Desjouy

---

## 1. Introduction

La bibliothèque standard fournit le module `contextlib` qui regroupe de nombreux outils dédiés aux *context managers*. Ce notebook donne quelques exemples d'utilisation des plus utiles.


## 2. Le décorateur `contextmanager`

La fonction `contextmanager` est un décorateur utilisé pour donner à une fonction le comportement d'un *context manager* sans avoir à implémenter une classe contenant `__enter_` et `__exit__`. Pour l'utiliser, il suffit de décorer une fonction génératrice qui appelle `yield` **une fois**. Tout ce qui se trouve avant le `yield` est considéré comme faisant partie de `__enter__` et tout ce qui est après est considéré comme faisant partie de `__exit__`. Par exemple:

In [1]:
import contextlib

@contextlib.contextmanager
def context():
    print('Entering')
    yield 'toto'
    print('Exiting')

In [2]:
with context():
    print("I'm in")

Entering
I'm in
Exiting


Un autre exemple permettant d'ouvrir et de lire des fichiers:

In [7]:
import contextlib

@contextlib.contextmanager
def open_file(filename, mode='r'):
    file = open(filename, mode)
    yield file
    file.close()

In [8]:
with open_file('quote.txt') as file:
    for line in file:
        print(line)

“Bad programmers worry about the code.

Good programmers worry about data structures and their relationships.”

― Linus Torvalds



## 3.  *Context manager* en tant que décorateur

Le module `contextlib` fournit également la classe de base `ContextDecorator` permettant d'utiliser un *context manager* comme un décorateur. Il suffit alors d'implémenter `__enter__` et `__exit__` dans une sous classe de `ContextDecorator`. 

In [20]:
import contextlib

class Context(contextlib.ContextDecorator):
    
    def __enter__(self):
        print('Entering')
        return self

    def __exit__(self, *exception):
        print('Exiting')
        return False

@Context()
def inside():
    print("I'm in!")

inside()

Entering
I'm in!
Exiting


## 4. Supprime les exceptions

Le *context manager* `supress()` permet simplement de supprimer une exception particulière si elle est levée dans le bloc indenté:

In [21]:
import contextlib

with contextlib.suppress(ZeroDivisionError):
    a = 1/0

### 5. Redirection de stdout ou stderr

Les *context managers* `redirect_stdout` et `redirect_stderr` permettent respectivement de rediriger `sys.stdout` (sortie standard) et `sys.stderr` (erreur standard) dans un autre objet. L'exemple suivant imbrique deux *context managers* pour rediriger `sys.stdout` dans un fichier:

In [12]:
import contextlib

with open('help.txt', 'w') as f:
    with contextlib.redirect_stdout(f):
        help(pow)

## 5. Et les autres...

* `AbstractContextManager`: classe abstraite de base qui implémente `__enter__()` qui retourne `self` et `__exit__()` qui retourne `None`

* `closing(thing)`: *context manager* qui ferme `thing` à la fin d'un bloc.

* `nullcontext(enter_result=None)`: *context manager* qui retourne `enter_result` depuis `__enter__`.
    
* `ExitStack`: *context manager* permettant de combiner facilement plusieurs *context managers* et des *cleanup functions*.

**Note:** *Le module `contextlib` fournit également toutes les variantes asynchrones (voir notebook sur `asyncio`) des objets cités ci dessus, à savoir `AbstractAsyncContextManager`, `asynccontextmanager`, et `AsyncExitStack`.*